# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

Import the dataset with: mongoimport --type json -d uk_food -c establishments --drop --jsonArray establishments.json

In [12]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [13]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [15]:
# confirm that our new database was created
print(mongo.list_database_names())


['admin', 'autosaurus', 'classDB', 'config', 'fruits_db', 'local', 'met', 'petsitly_marketing', 'test', 'testdb', 'travel_db', 'uk_food']


In [16]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [17]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [18]:
# review the collections in our new database
print(db.establishments)

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'uk_food'), 'establishments')


In [19]:
# review a document in the establishments collection
pprint(db.establishments.find_one())

{'AddressLine1': 'The Bay',
 'AddressLine2': 'St Margarets Bay',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'BusinessName': 'The Coastguard Inn',
 'BusinessType': 'Pub/bar/nightclub',
 'BusinessTypeID': 7843,
 'ChangesByServerID': 0,
 'Distance': 4587.347174863443,
 'FHRSID': 1034540,
 'LocalAuthorityBusinessID': 'PI/000078691',
 'LocalAuthorityCode': '182',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT15 6DY',
 'RatingDate': '2022-08-17T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64c3a78f66f358ca84482a5f'),
 'geocode': {'latitude': '51.152225', 'longitude': '1.387974'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1034540',
            'rel': 'self'}],
 'meta': {'dataSource': None,
          'extractDate': '0001-01-01T0

In [20]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [21]:
# Create a dictionary for the new restaurant data
new_restaurant = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [22]:
# Insert the new restaurant into the collection
establishments.insert_one(new_restaurant)

In [23]:
# Check that the new restaurant was inserted
for doc in establishments.find({'BusinessName': 'Penang Flavours'}):
    print(doc)

{'_id': ObjectId('64c3a7ad741b7855c794f18a'), 'BusinessName': 'Penang Flavours', 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': '', 'AddressLine1': 'Penang Flavours', 'AddressLine2': '146A Plumstead Rd', 'AddressLine3': 'London', 'AddressLine4': '', 'PostCode': 'SE18 7DY', 'Phone': '', 'LocalAuthorityCode': '511', 'LocalAuthorityName': 'Greenwich', 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk', 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk', 'scores': {'Hygiene': '', 'Structural': '', 'ConfidenceInManagement': ''}, 'SchemeType': 'FHRS', 'geocode': {'longitude': '0.08384000', 'latitude': '51.49014200'}, 'RightToReply': '', 'Distance': 4623.972328074718, 'NewRatingPending': True}


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [24]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
query = {'BusinessName': 'Penang Flavours'}
fields = {'BusinessTypeID': 1, 'BusinessType': 1}
for doc in establishments.find(query,fields):
    print(doc)

{'_id': ObjectId('64c3a7ad741b7855c794f18a'), 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': ''}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [25]:
# Update the new restaurant with the correct BusinessTypeID
query = {'BusinessName': 'Penang Flavours'}
db.establishments.update_one(query, {'$set': {'BusinessTypeID': 1}})

In [26]:
# Confirm that the new restaurant was updated
for doc in establishments.find({'BusinessName': 'Penang Flavours'}):
    print(doc['BusinessTypeID'])

1


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [27]:
# Find how many documents have LocalAuthorityName as "Dover"
local_auth = establishments.count_documents({'LocalAuthorityName':{'$in':['Dover']}})
local_auth

994

In [28]:
# Delete all documents where LocalAuthorityName is "Dover"
establishments.delete_many({'LocalAuthorityName':{'$in':['Dover']}})

In [29]:
# Check if any remaining documents include Dover
local_auth = establishments.count_documents({'LocalAuthorityName':{'$in':['Dover']}})
local_auth

0

In [30]:
# Check that other documents remain with 'find_one'
establishments.find_one()

{'_id': ObjectId('64c3a78f66f358ca84482d46'),
 'FHRSID': 1043695,
 'ChangesByServerID': 0,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'PostCode': 'CT19 6BL',
 'Phone': '',
 'RatingValue': '5',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingDate': '2018-04-04T00:00:00',
 'LocalAuthorityCode': '188',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'scores': {'Hygiene': 5, 'Structural': 5, 'ConfidenceInManagement': 5},
 'SchemeType': 'FHRS',
 'geocode': {'longitude': '1.195625', 'latitude': '51.083812'},
 'RightToReply': '',
 'Distance': 4591.765489457773,
 'NewRatingPending': False,
 'meta': {'dataSource': None,
  'extractDate': '0001-01-01

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [31]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many({}, [ {'$set':{ "geocode.latitude" : {'$toDouble': "$geocode.latitude"}}} ])
establishments.update_many({}, [ {'$set':{ "geocode.longitude" : {'$toDouble': "$geocode.longitude"}}} ])

Use `update_many` to convert `RatingValue` to integer numbers.

In [32]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

In [33]:
# Change the data type from String to Integer for RatingValue
establishments.update_many({}, [ {'$set':{ "RatingValue" : {'$toInt': "$RatingValue"}}} ])

In [34]:
# Check that the coordinates and rating value are now numbers
# establishments.find_one(["geocode.latitude","geocode.longitude","RatingValue"])
query = {}
fields = {"geocode.latitude":1,"geocode.longitude":1,"RatingValue":1}

# Capture the results to a variable
results = establishments.find(query, fields)

# Pretty print the results
for result in results:
    pprint(result)

{'RatingValue': 5,
 '_id': ObjectId('64c3a78f66f358ca84482d46'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625}}
{'RatingValue': 5,
 '_id': ObjectId('64c3a78f66f358ca84482d48'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'RatingValue': 4,
 '_id': ObjectId('64c3a78f66f358ca84482d49'),
 'geocode': {'latitude': 51.086058, 'longitude': 1.196408}}
{'RatingValue': 4,
 '_id': ObjectId('64c3a78f66f358ca84482d4a'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'RatingValue': 5,
 '_id': ObjectId('64c3a78f66f358ca84482d4b'),
 'geocode': {'latitude': 51.0783519967076, 'longitude': 1.18590330311705}}
{'RatingValue': 4,
 '_id': ObjectId('64c3a78f66f358ca84482d4c'),
 'geocode': {'latitude': 51.0783519967076, 'longitude': 1.18590330311705}}
{'RatingValue': 5,
 '_id': ObjectId('64c3a78f66f358ca84482d4d'),
 'geocode': {'latitude': 51.0783519967076, 'longitude': 1.18590330311705}}
{'RatingValue': 5,
 '_id': ObjectId('64c3a78f66f358ca84482d4e'),
 'geocode': {'lat